# Optimize Initial Conditions
## Yabox

In [2]:
from scipy.optimize import brute
import numpy as np
from datetime import datetime,timedelta
import pandas as pd
from yabox import DE

# Initialize Ray

In [3]:
from environs import Env
env = Env()
env.str("CUDA_DEVICE_ORDER",'PCI_BUS_ID')
env.int("CUDA_VISIBLE_DEVICES",1)
env.int("NUMBA_ENABLE_CUDASIM",1)
env.bool("OMPI_MCA_opal_cuda_support",True)

import os
import ray
MB=1024*1024
GB=MB*1024
ray.shutdown()
ray.init(object_store_memory=1*GB,memory=1*GB,
         #lru_evict=True,
         driver_object_store_memory=500*MB,num_gpus=4,num_cpus=10,
         ignore_reinit_error=True) # , include_webui=False, ignore_reinit_error=True)

@ray.remote(num_gpus=1)
def use_gpu():
    print("ray.get_gpu_ids(): {}".format(ray.get_gpu_ids()[0]))
    print("CUDA_VISIBLE_DEVICES: {}".format(os.environ["CUDA_VISIBLE_DEVICES"]))

use_gpu.remote()

2020-07-28 11:14:35,159	INFO resource_spec.py:212 -- Starting Ray with 0.98 GiB memory available for workers and up to 1.0 GiB for objects. You can adjust these settings with ray.init(memory=<bytes>, object_store_memory=<bytes>).
2020-07-28 11:14:35,590	INFO services.py:1170 -- View the Ray dashboard at localhost:8266


ObjectID(45b95b1c8bd3a9c4ffffffff010000c801000000)

(pid=29409) ray.get_gpu_ids(): 3
(pid=29409) CUDA_VISIBLE_DEVICES: 3


# Load New and Process Data from website data.brasil.io

In [4]:
import get_data
LoadData=True

if LoadData:
    get_data.get_data()

Baixando arquivos brasil.io...


# Functions to Load Processed Data

In [5]:
def load_confirmed(districtRegion, start_date):
    dateparse = lambda x: datetime.strptime(x, '%Y-%m-%d')
    df = pd.read_csv('./data/DRS_confirmados.csv',delimiter=',',parse_dates=True, date_parser=dateparse)
    y=[]
    x=[]
    for i in range(0,len(df.date)):
        y.append(df[districtRegion].values[i])
        x.append(df.date.values[i])
    df2=pd.DataFrame(data=y,index=x,columns=[""])
    df2=df2[start_date:]
    del x,y,df,dateparse
    return df2

def load_dead(districtRegion, start_date):
    dateparse = lambda x: datetime.strptime(x, '%Y-%m-%d')
    df = pd.read_csv('./data/DRS_mortes.csv',delimiter=',',parse_dates=True, date_parser=dateparse)
    y=[]
    x=[]
    for i in range(0,len(df.date)):
        y.append(df[districtRegion].values[i])
        x.append(df.date.values[i])
    df2=pd.DataFrame(data=y,index=x,columns=[""])
    df2=df2[start_date:]
    del x,y,df,dateparse
    return df2

# Load solver

In [6]:
import LearnerICRayNoLoadBH as L 

# Data for States

In [7]:
dfparam = pd.read_csv("data/param.csv")
dfPopEst = pd.read_csv("data/DRS_popEst.csv")
dfparam['popEst']=dfPopEst.popEst
display(dfparam)

DRS  start-date  prediction-range         s0  \
0        DRS 01 - Grande São Paulo  2020-03-20               200  2000000.0   
1               DRS 02 - Araçatuba  2020-04-01               200      500.0   
2              DRS 03 - Araraquara  2020-04-01               200     2000.0   
3        DRS 04 - Baixada Santista  2020-04-01               200     8000.0   
4                DRS 05 - Barretos  2020-04-01               200     2000.0   
5                   DRS 06 - Bauru  2020-04-01               200    10000.0   
6                DRS 07 - Campinas  2020-04-01               200    20000.0   
7                  DRS 08 - Franca  2020-04-01               200     1000.0   
8                 DRS 09 - Marília  2020-04-01               200     5000.0   
9              DRS 10 - Piracicaba  2020-04-01               200    10000.0   
10    DRS 11 - Presidente Prudente  2020-04-01               200     1000.0   
11               DRS 12 - Registro  2020-04-01               200     1000.0   
12         DRS 13 - Ribeirão Preto  2020-04-01               200     5000.0   
13  DRS 14 - São João da Boa Vista  2020-04-01               200     2000.0   
14  DRS 15 - São José do Rio Preto  2020-04-01               200    10000.0   
15               DRS 16 - Sorocaba  2020-04-01               200     1200.0   
16                DRS 17 - Taubaté  2020-04-01               200    10000.0   

        e0      a0        i0        r0        d0  START  RATIO  WCASES  WREC  \
0   0.0001  0.0001  800.0000  300.0000  400.0000      0   0.15    0.15  0.05   
1   0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
2   0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
3   0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
4   0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
5   0.0001  0.0001    4.0000    0.0001    0.0001      0   0.15    0.40  0.10   
6   0.0001  0.0001   40.0000    0.0001    0.0001      0   0.15    0.40  0.10   
7   0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
8   0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
9   0.0001  0.0001    0.0001    0.0001    1.0000      0   0.15    0.40  0.10   
10  0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
11  0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
12  0.0001  0.0001    0.0001    0.0001    0.0001      5   0.15    0.40  0.10   
13  0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
14  0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
15  0.0001  0.0001    2.0000    0.0001    0.0001      0   0.15    0.40  0.10   
16  0.0001  0.0001   17.0000    0.0001    2.0000      0   0.15    0.40  0.10   

        popEst  
0   21702084.0  
1     791256.0  
2    1025982.0  
3    1865397.0  
4     440907.0  
5    1800757.0  
6    4671287.0  
7     713458.0  
8    1144665.0  
9    1586546.0  
10    775627.0  
11    284509.0  
12   1523682.0  
13    834872.0  
14   1629470.0  
15   2530829.0  
16   2548463.0

In [8]:
dfSP = pd.read_csv("data/dados_municipios_SP.csv")

# lista DRSs
DRS = list(dfSP["DRS"].unique())
DRS.remove("Indefinido")

dfSP

date state   city place_type  confirmed  deaths  order_for_place  \
0      2020-07-27    SP  TOTAL      state     487654   21676              152   
1      2020-07-26    SP  TOTAL      state     483982   21606              151   
2      2020-07-25    SP  TOTAL      state     479481   21517              150   
3      2020-07-24    SP  TOTAL      state     463218   21206              149   
4      2020-07-23    SP  TOTAL      state     452007   20894              148   
...           ...   ...    ...        ...        ...     ...              ...   
55411  2020-06-23    SP   Óleo       city          1       0                5   
55412  2020-06-22    SP   Óleo       city          1       0                4   
55413  2020-06-21    SP   Óleo       city          1       0                3   
55414  2020-06-20    SP   Óleo       city          1       0                2   
55415  2020-06-19    SP   Óleo       city          1       0                1   

       is_last      popEst  city_ibge_code  confirmed_per_100k_inhabitants  \
0         True  45919049.0            35.0                      1061.98628   
1        False  45919049.0            35.0                      1053.98960   
2        False  45919049.0            35.0                      1044.18757   
3        False  45919049.0            35.0                      1008.77089   
4        False  45919049.0            35.0                       984.35619   
...        ...         ...             ...                             ...   
55411    False      2496.0       3533809.0                        40.06410   
55412    False      2496.0       3533809.0                        40.06410   
55413    False      2496.0       3533809.0                        40.06410   
55414    False      2496.0       3533809.0                        40.06410   
55415    False      2496.0       3533809.0                        40.06410   

       death_rate               DRS  
0          0.0444        Indefinido  
1          0.0446        Indefinido  
2          0.0449        Indefinido  
3          0.0458        Indefinido  
4          0.0462        Indefinido  
...           ...               ...  
55411      0.0000  DRS 09 - Marília  
55412      0.0000  DRS 09 - Marília  
55413      0.0000  DRS 09 - Marília  
55414      0.0000  DRS 09 - Marília  
55415      0.0000  DRS 09 - Marília  

[55416 rows x 13 columns]

# Functions for Optimization

In [9]:
from scipy.integrate import odeint
import sys
import io
import gc

def create_f(districtRegion,e0,a0,r0,date, ratio, predict_range, version):
                
    def fobjective(point):
        
        dead=  load_dead(districtRegion,date)
        data = load_confirmed(districtRegion,date)*(1-ratio)-dead
        cleanRecovered=False
        s0, deltaDate, i0, d0, startNCases, weigthCases, weigthRecov = point
        end_date=datetime.strptime(date, "%Y-%m-%d") + timedelta(days=deltaDate)
        f=L.Learner.remote(districtRegion, end_date.strftime("%Y-%m-%d"), predict_range,\
                           s0, e0, a0, i0, r0, d0, startNCases, ratio, weigthCases, weigthRecov, \
                           cleanRecovered, version, data, dead, savedata=False)
        result = f.train.remote() 
        result = ray.get(result) 

        del end_date,cleanRecovered, data, dead, point,f         

        gc.collect()

        return result
    return fobjective

In [10]:
@ray.remote(memory=50 * 1024 * 1024, max_calls=1)
def opt(districtRegion,s0,i0,e0,a0,r0,d0,wcases,date,startNCases, ratio, predict_range, popEst, version):

    bounds=[(0.1*popEst,0.9*popEst),(-2,2),(0,4000), (0,1000), (0,250),\
              (0.3,0.8),(0.02,0.08)]
    maxiterations=500
    f=create_f(districtRegion,e0,a0,r0,date, ratio, predict_range, version)
    de = DE(f, bounds, maxiters=maxiterations)
    for step in de.geniterator():
        try:
            idx = step.best_idx
            norm_vector = step.population[idx]
            best_params = de.denormalize([norm_vector])
            del norm_vector, idx
        except:
            print("error in function evaluation")
    p=best_params[0]
    del f, bounds, data, dead,best_params
    
    return p

# Main Code

In [11]:
%%javascript
IPython.OutputArea.prototype._should_scroll = function(lines){
    return true;}

<IPython.core.display.Javascript object>

In [27]:
DRS=dfparam.DRS
display(DRS)
allDRS=True
version="106"
gc.enable()

optimal=[]
if allDRS:
    for districtRegion in DRS:
        #remove previous history file
        strFile='./results/history_'+districtRegion+version+'.csv'
        if os.path.isfile(strFile):
            os.remove(strFile)
        query = dfparam.query('DRS == "{}"'.format(districtRegion)).reset_index()
        parameters = np.array(query.iloc[:, 2:])[0]
        date,predict_range,s0,e0,a0,i0,r0,d0,startNCases,ratio,wcases,wrec,popEst = parameters
        optimal.append(opt.remote(districtRegion,s0,i0,e0,a0,r0,d0,wcases,date,startNCases, \
                                  ratio, predict_range, popEst, version))        
else:
    districtRegion = "DRS 01 - Grande São Paulo" #'DRS 08 - Franca' \
    #'DRS 14 - São João da Boa Vista' #'DRS 04 - Baixada Santista' \
    #'DRS 11 - Presidente Prudente' #'DRS 13 - Ribeirão Preto' \
    #'DRS 05 - Barretos' #'DRS 12 - Registro' #'DRS 15 - São José do Rio Preto' \
    #'DRS 10 - Piracicaba'#'DRS 17 - Taubaté'#'DRS 02 - Araçatuba'# \
    #'DRS 03 - Araraquara' #DRS 07 - Campinas'#'DRS 16 - Sorocaba'#'DRS 06 - Bauru' \
    #'DRS 09 - Marília' #"DRS 01 - Grande São Paulo"

    #remove previous history file
    strFile='./results/history_'+districtRegion+version+'.csv'
    if os.path.isfile(strFile):
        os.remove(strFile)
    query = dfparam.query('DRS == "{}"'.format(districtRegion)).reset_index()
    parameters = np.array(query.iloc[:, 2:])[0]
    date,predict_range,s0,e0,a0,i0,r0,d0,startNCases,ratio,wcases,wrec,popEst = parameters
    optimal.append(opt.remote(districtRegion,s0,i0,e0,a0,r0,d0,wcasesdate,startNCases, \
                              ratio, predict_range, popEst, version))        

0          DRS 01 - Grande São Paulo
1                 DRS 02 - Araçatuba
2                DRS 03 - Araraquara
3          DRS 04 - Baixada Santista
4                  DRS 05 - Barretos
5                     DRS 06 - Bauru
6                  DRS 07 - Campinas
7                    DRS 08 - Franca
8                   DRS 09 - Marília
9                DRS 10 - Piracicaba
10      DRS 11 - Presidente Prudente
11                 DRS 12 - Registro
12           DRS 13 - Ribeirão Preto
13    DRS 14 - São João da Boa Vista
14    DRS 15 - São José do Rio Preto
15                 DRS 16 - Sorocaba
16                  DRS 17 - Taubaté
Name: DRS, dtype: object

(pid=34156) basinhopping step 7: f 674217 trial_f 1.23238e+06 accepted 0  lowest_f 674217
(pid=34203) basinhopping step 5: f 615491 trial_f 7.91743e+10 accepted 0  lowest_f 615491
(pid=34288) basinhopping step 0: f 9.20712e+06
(pid=33928) basinhopping step 5: f -6.94252e+11 trial_f 1.70245e+08 accepted 0  lowest_f -6.94252e+11
(pid=33690) basinhopping step 9: f -1.05302e+12 trial_f 7.14138e+09 accepted 0  lowest_f -1.05302e+12
(pid=34079) basinhopping step 4: f -1.683e+10 trial_f 5.34209e+06 accepted 0  lowest_f -1.683e+10
(pid=34156) basinhopping step 8: f 674217 trial_f 1.66076e+11 accepted 0  lowest_f 674217


In [28]:
optimal=ray.get(optimal)


(pid=34288) basinhopping step 1: f 9.20712e+06 trial_f 5.25182e+11 accepted 0  lowest_f 9.20712e+06
(pid=33690) basinhopping step 10: f -1.05302e+12 trial_f 3.54659e+08 accepted 0  lowest_f -1.05302e+12
(pid=33928) basinhopping step 6: f -6.94252e+11 trial_f 8.15474e+08 accepted 0  lowest_f -6.94252e+11
(pid=33925) basinhopping step 5: f -1.32676e+12 trial_f 9.00528e+08 accepted 0  lowest_f -1.32676e+12
(pid=34203) basinhopping step 6: f 615491 trial_f 5.11768e+08 accepted 0  lowest_f 615491
(pid=34157) basinhopping step 1: f -1.28121e+11 trial_f 1.54907e+09 accepted 0  lowest_f -1.28121e+11
(pid=33924) basinhopping step 7: f 1.58103e+06 trial_f 4.65008e+08 accepted 0  lowest_f 1.58103e+06
(pid=33928) basinhopping step 7: f -6.94252e+11 trial_f 4.10417e+11 accepted 0  lowest_f -6.94252e+11
(pid=33939) basinhopping step 10: f -4.88674e+06 trial_f 1.12551e+07 accepted 0  lowest_f -4.88674e+06
(pid=33923) basinhopping step 8: f -7.73241e+13 trial_f 2.53209e+11 accepted 0  lowest_f -7.7324

2020-07-28 11:35:06,414	WARNING worker.py:1090 -- WARNING: 40 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.
2020-07-28 11:35:06,415	WARNING worker.py:1090 -- WARNING: 41 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.


(pid=33687) basinhopping step 10: f -9.94986e+10 trial_f 1.29247e+08 accepted 0  lowest_f -9.94986e+10
(pid=33707) basinhopping step 6: f -3.99016e+09 trial_f 3.64867e+08 accepted 0  lowest_f -3.99016e+09
(pid=34079) basinhopping step 5: f -1.683e+10 trial_f 1.09778e+08 accepted 0  lowest_f -1.683e+10
(pid=33925) basinhopping step 6: f -1.32676e+12 trial_f 2.115e+10 accepted 0  lowest_f -1.32676e+12
(pid=34078) basinhopping step 4: f -1.81424e+10 trial_f 2.2946e+07 accepted 0  lowest_f -1.81424e+10
(pid=33925) basinhopping step 7: f -1.32676e+12 trial_f 7.96351e+11 accepted 0  lowest_f -1.32676e+12
(pid=34078) basinhopping step 5: f -1.81424e+10 trial_f 6.17733e+09 accepted 0  lowest_f -1.81424e+10
(pid=34203) basinhopping step 7: f 615491 trial_f 2.33437e+11 accepted 0  lowest_f 615491
(pid=33925) basinhopping step 8: f -1.32676e+12 trial_f 2.99258e+07 accepted 0  lowest_f -1.32676e+12
(pid=34078) basinhopping step 6: f -1.81424e+10 trial_f 6.17733e+09 accepted 0  lowest_f -1.81424e+1

2020-07-28 11:35:13,051	WARNING worker.py:1090 -- WARNING: 40 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.
2020-07-28 11:35:13,052	WARNING worker.py:1090 -- WARNING: 41 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.


(pid=34203) basinhopping step 8: f 615491 trial_f 950291 accepted 0  lowest_f 615491
(pid=34288) basinhopping step 2: f 9.20712e+06 trial_f 4.58647e+08 accepted 0  lowest_f 9.20712e+06
(pid=34239) basinhopping step 4: f 898930 trial_f 6.61304e+08 accepted 0  lowest_f 898930
(pid=33922) basinhopping step 3: f -1.23111e+10 trial_f -1.23111e+10 accepted 1  lowest_f -1.23111e+10
(pid=33922) found new global minimum on step 3 with function value -1.23111e+10
(pid=34339) basinhopping step 2: f -1.21163e+12 trial_f 6.29577e+08 accepted 0  lowest_f -1.21163e+12
(pid=34157) basinhopping step 2: f -1.28121e+11 trial_f 1.53429e+09 accepted 0  lowest_f -1.28121e+11
(pid=34287) basinhopping step 0: f -8.19139e+10
(pid=33922) basinhopping step 4: f -1.23111e+10 trial_f 4.10874e+06 accepted 0  lowest_f -1.23111e+10
(pid=33922) basinhopping step 5: f -1.23111e+10 trial_f 1.78336e+06 accepted 0  lowest_f -1.23111e+10
(pid=34288) basinhopping step 3: f 9.20712e+06 trial_f 5.25184e+11 accepted 0  lowest_

KeyboardInterrupt: 

In [ ]:
for i in range(0,len(DRS)):    

    districtRegion=DRS[i]
    query = dfparam.query('DRS == "{}"'.format(districtRegion)).reset_index()
    parameters = np.array(query.iloc[:, 2:])[0]
    startdate,predict_range,s0,e0,a0,i0,r0,d0,startNCases,ratio,wcases,wrec = parameters
    Date = datetime.strptime(startdate, "%Y-%m-%d")
    end_date = Date + timedelta(days=+int(optimal[i][1]))
    dateStr=end_date.strftime("%Y-%m-%d")

    j = query['index'].values[0]
    dfparam.at[j, "s0"] = optimal[i][0]
    dfparam.at[j, "start-date"] = dateStr
    dfparam.at[j, "i0"] = optimal[i][2]
    dfparam.at[j, "WCASES"] = optimal[i][3]
    dfparam.at[j, "WREC"] = optimal[i][4]

    dfparam.to_csv("data/param_optimized_Yabox.csv", sep=",", index=False)
    dfparam
    

(pid=127916) basinhopping step 7: f 1.71663e+07 trial_f 6.76594e+13 accepted 0  lowest_f 1.71663e+07
(pid=127865) warning: basinhopping: local minimization failure
(pid=127865) basinhopping step 10: f 6.53304e+07 trial_f 6.58457e+07 accepted 0  lowest_f 6.53304e+07
(pid=128090) basinhopping step 0: f 3.11696e+06
(pid=127962) basinhopping step 4: f 1.81521e+06 trial_f 3.72377e+11 accepted 0  lowest_f 1.81521e+06
(pid=127930) warning: basinhopping: local minimization failure
(pid=127930) basinhopping step 9: f -3.15296e+14 trial_f 7.96738e+13 accepted 0  lowest_f -3.15296e+14
(pid=128064) basinhopping step 4: f 2.08375e+07 trial_f 2.12689e+07 accepted 0  lowest_f 1.98516e+07
(pid=127930) basinhopping step 10: f -3.15296e+14 trial_f 7.96737e+13 accepted 0  lowest_f -3.15296e+14
(pid=128116) basinhopping step 0: f 7.09059e+07
(pid=128090) basinhopping step 1: f 1.40126e+06 trial_f 1.40126e+06 accepted 1  lowest_f 1.40126e+06
(pid=128090) found new global minimum on step 1 with function val

2020-07-28 06:39:58,891	WARNING worker.py:1090 -- WARNING: 34 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.
2020-07-28 06:39:58,894	WARNING worker.py:1090 -- WARNING: 35 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.


(pid=128116) /home/ats4i/anaconda3/envs/geo_env/lib/python3.6/site-packages/scipy/integrate/odepack.py:248: ODEintWarning: Excess work done on this call (perhaps wrong Dfun type). Run with full_output = 1 to get quantitative information.
(pid=128116)   warnings.warn(warning_msg, ODEintWarning)
(pid=128090) basinhopping step 2: f 1.40126e+06 trial_f 3.11692e+06 accepted 0  lowest_f 1.40126e+06
(pid=127962) basinhopping step 5: f 1.81521e+06 trial_f 1.81521e+06 accepted 1  lowest_f 1.81521e+06
(pid=127962) /home/ats4i/anaconda3/envs/geo_env/lib/python3.6/site-packages/scipy/integrate/odepack.py:248: ODEintWarning: Excess work done on this call (perhaps wrong Dfun type). Run with full_output = 1 to get quantitative information.
(pid=127962)   warnings.warn(warning_msg, ODEintWarning)
(pid=127963) basinhopping step 8: f -1.79932e+14 trial_f 1.85695e+07 accepted 0  lowest_f -1.79932e+14
(pid=127959) basinhopping step 9: f -1.58911e+11 trial_f 1.25209e+13 accepted 0  lowest_f -1.58911e+11
(p

2020-07-28 06:40:10,234	WARNING worker.py:1090 -- WARNING: 34 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.
2020-07-28 06:40:10,237	WARNING worker.py:1090 -- WARNING: 35 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.


(pid=127962) basinhopping step 8: f 1.81521e+06 trial_f 8.39321e+10 accepted 0  lowest_f 1.81521e+06
(pid=128145) basinhopping step 2: f 3.46194e+11 trial_f 4.02489e+12 accepted 0  lowest_f 3.46194e+11
(pid=127961) warning: basinhopping: local minimization failure
(pid=127961) basinhopping step 8: f 9.71123e+06 trial_f 2.60725e+14 accepted 0  lowest_f 9.71123e+06
(pid=127958) basinhopping step 7: f -1.04601e+14 trial_f 9.53431e+06 accepted 0  lowest_f -1.04601e+14
(pid=128143) basinhopping step 0: f -1.37143e+14
(pid=127959) basinhopping step 10: f -1.58911e+11 trial_f -1.15119e+11 accepted 0  lowest_f -1.58911e+11
(pid=127963) basinhopping step 10: f -1.79932e+14 trial_f 3.84728e+11 accepted 0  lowest_f -1.79932e+14
(pid=128063) basinhopping step 2: f -3.95187e+13 trial_f 6.67005e+10 accepted 0  lowest_f -3.95187e+13


...

(pid=14549) /home/ats4i/anaconda3/envs/geo_env/lib/python3.6/site-packages/scipy/integrate/odepack.py:248: ODEintWarning: Excess work done on this call (perhaps wrong Dfun type). Run with full_output = 1 to get quantitative information.
(pid=14549)   warnings.warn(warning_msg, ODEintWarning)
(pid=14544) basinhopping step 8: f 636107 trial_f 5.11611e+11 accepted 0  lowest_f 636107
(pid=14649) basinhopping step 0: f 2.03338e+07
(pid=14546) basinhopping step 1: f -6.29382e+13 trial_f 2.78496e+12 accepted 0  lowest_f -6.29382e+13
(pid=14332) basinhopping step 8: f -5.90168e+13 trial_f 8.70252e+12 accepted 0  lowest_f -5.90168e+13
(pid=14548) basinhopping step 2: f -3.9509e+14 trial_f -3.9509e+14 accepted 1  lowest_f -3.9509e+14
(pid=14548) found new global minimum on step 2 with function value -3.9509e+14
(pid=14550) basinhopping step 5: f 963344 trial_f 2.36603e+13 accepted 0  lowest_f 963344
(pid=14544) basinhopping step 9: f 636107 trial_f 1.53205e+14 accepted 0  lowest_f 636107
(pid=14

2020-07-28 10:06:12,663	WARNING worker.py:1090 -- WARNING: 34 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.
2020-07-28 10:06:12,665	WARNING worker.py:1090 -- WARNING: 35 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.


(pid=14518) basinhopping step 4: f -3.66781e+14 trial_f -3.66781e+14 accepted 1  lowest_f -3.66781e+14
(pid=14518) found new global minimum on step 4 with function value -3.66781e+14
(pid=14549) basinhopping step 3: f -3.52365e+14 trial_f 1.5401e+11 accepted 0  lowest_f -3.52365e+14
(pid=14518) basinhopping step 5: f -3.66781e+14 trial_f 3.1507e+06 accepted 0  lowest_f -3.66781e+14
(pid=14545) basinhopping step 5: f 1.39711e+06 trial_f 1.71136e+11 accepted 0  lowest_f 1.39711e+06
(pid=14545) basinhopping step 6: f 1.39711e+06 trial_f 1.71139e+11 accepted 0  lowest_f 1.39711e+06
(pid=14662) basinhopping step 0: f 2.06608e+06
(pid=14547) basinhopping step 7: f 905282 trial_f 3.92711e+12 accepted 0  lowest_f 905282
(pid=14549) warning: basinhopping: local minimization failure
(pid=14549) basinhopping step 4: f -3.52365e+14 trial_f 3.60084e+06 accepted 0  lowest_f -3.52365e+14
(pid=14545) warning: basinhopping: local minimization failure
(pid=14545) basinhopping step 7: f 1.39711e+06 trial

2020-07-28 10:06:25,401	WARNING worker.py:1090 -- WARNING: 34 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.


(pid=14550) basinhopping step 9: f -4.01451e+14 trial_f -2.69723e+13 accepted 0  lowest_f -4.01451e+14
